In [2]:
pip install geopy

     |████████████████████████████████| 102kB 2.2MB/s ta 0:00:01
Note: you may need to restart the kernel to use updated packages.


In [3]:
pip install bs4

     |████████████████████████████████| 102kB 7.5MB/s ta 0:00:011
  Stored in directory: /home/jupyterlab/.cache/pip/wheels/a0/b0/b2/4f80b9456b87abedbc0bf2d52235414c3467d8889be38dd472
Successfully built bs4
Note: you may need to restart the kernel to use updated packages.


In [4]:
pip install lxml

     |████████████████████████████████| 5.8MB 26.6MB/s eta 0:00:01
Note: you may need to restart the kernel to use updated packages.


In [5]:
pip install geocoder

     |████████████████████████████████| 102kB 1.6MB/s ta 0:00:01
     |████████████████████████████████| 829kB 6.9MB/s eta 0:00:01
     |████████████████████████████████| 81kB 18.0MB/s eta 0:00:01
  Stored in directory: /home/jupyterlab/.cache/pip/wheels/0c/61/d2/d6b7317325828fbb39ee6ad559dbe4664d0896da4721bf379e
Successfully built future
Note: you may need to restart the kernel to use updated packages.


In [6]:
import numpy as np # library to handle data in a vectorized manner

import pandas as pd # library for data analsysis
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)

import json # library to handle JSON files

#!conda install -c conda-forge geopy --yes # uncomment this line if you haven't completed the Foursquare API lab
from geopy.geocoders import Nominatim # convert an address into latitude and longitude values

import requests # library to handle requests
from pandas.io.json import json_normalize # tranform JSON file into a pandas dataframe

# Matplotlib and associated plotting modules
import matplotlib.cm as cm
import matplotlib.colors as colors

# import k-means from clustering stage
from sklearn.cluster import KMeans

#!conda install -c conda-forge folium=0.5.0 --yes # uncomment this line if you haven't completed the Foursquare API lab
import folium # map rendering library

#import beatutifulsoup
import requests
from bs4 import BeautifulSoup

print('Libraries imported.')

Libraries imported.


In [7]:
#Read in the Chicago_data.csv file
import pandas
illinois_df = pd.read_csv("chicago_data_2.csv", sep=";")
columns = ['Geo Point','Geo Shape', 'RegionID']
illinois_df.drop(columns, inplace=True, axis=1)


#rename the columns 
illinois_df.columns = ['State', 'County', 'City', 'Neighborhood']
illinois_df.head(10)

State     County     City      Neighborhood
0    IL       Cook  Chicago     Brighton Park
1    IL       Cook  Chicago  Stateway Gardens
2    IL       Cook  Chicago        Ravenswood
3    IL       Cook  Chicago   Parkway Gardens
4    IL       Cook  Chicago       South Shore
5    IL       Cook  Chicago   Washington Park
6    IL    Du Page   Aurora  Southeast Aurora
7    IL       Cook  Chicago       Hanson Park
8    IL       Cook  Chicago   Belmont Terrace
9    IL  Champaign   Urbana          Downtown

In [8]:
#filter by 'Chicago' to get all the neighborhoods in the city of Chicago
chicago_df = illinois_df[illinois_df['City'].str.contains('Chicago')]
chicago_df = chicago_df.reset_index(drop=True)
chicago_df.head(15)


State County     City      Neighborhood
0     IL   Cook  Chicago     Brighton Park
1     IL   Cook  Chicago  Stateway Gardens
2     IL   Cook  Chicago        Ravenswood
3     IL   Cook  Chicago   Parkway Gardens
4     IL   Cook  Chicago       South Shore
5     IL   Cook  Chicago   Washington Park
6     IL   Cook  Chicago       Hanson Park
7     IL   Cook  Chicago   Belmont Terrace
8     IL   Cook  Chicago    Heart of Italy
9     IL   Cook  Chicago          The Bush
10    IL   Cook  Chicago       Rogers Park
11    IL   Cook  Chicago      Clearing (E)
12    IL   Cook  Chicago        South Loop
13    IL   Cook  Chicago      Pulaski Park
14    IL   Cook  Chicago     Kilbourn Park

In [9]:
address = 'Chicago, IL'

geolocator = Nominatim()
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinate of Chicago are {}, {}.'.format(latitude, longitude))

/home/jupyterlab/conda/envs/python/lib/python3.6/site-packages/ipykernel_launcher.py:3: DeprecationWarning: Using Nominatim with the default "geopy/1.20.0" `user_agent` is strongly discouraged, as it violates Nominatim's ToS https://operations.osmfoundation.org/policies/nominatim/ and may possibly cause 403 and 429 HTTP errors. Please specify a custom `user_agent` with `Nominatim(user_agent="my-application")` or by overriding the default `user_agent`: `geopy.geocoders.options.default_user_agent = "my-application"`. In geopy 2.0 this will become an exception.
  This is separate from the ipykernel package so we can avoid doing imports until


The geograpical coordinate of Chicago are 41.8755616, -87.6244212.


In [10]:
import geocoder

def get_latlng(neighborhood):
    # initialize your variable to None
    lat_lng_coords = None
    # loop until you get the coordinates
    while(lat_lng_coords is None):
        g = geocoder.arcgis('{}, Chicago, Illinois'.format(neighborhood))
        lat_lng_coords = g.latlng
    return lat_lng_coords
    
get_latlng('Brighton Park')

[41.818610000000035, -87.69947999999994]

In [11]:
neighborhoods = chicago_df['Neighborhood']
coordinates = [get_latlng(neighborhood) for neighborhood in neighborhoods.tolist()]
print('done!')

Status code Unknown from https://geocode.arcgis.com/arcgis/rest/services/World/GeocodeServer/find: ERROR - HTTPSConnectionPool(host='geocode.arcgis.com', port=443): Read timed out. (read timeout=5.0)
Status code Unknown from https://geocode.arcgis.com/arcgis/rest/services/World/GeocodeServer/find: ERROR - HTTPSConnectionPool(host='geocode.arcgis.com', port=443): Read timed out. (read timeout=5.0)
Status code Unknown from https://geocode.arcgis.com/arcgis/rest/services/World/GeocodeServer/find: ERROR - HTTPSConnectionPool(host='geocode.arcgis.com', port=443): Read timed out. (read timeout=5.0)
Status code Unknown from https://geocode.arcgis.com/arcgis/rest/services/World/GeocodeServer/find: ERROR - HTTPSConnectionPool(host='geocode.arcgis.com', port=443): Read timed out. (read timeout=5.0)
Status code Unknown from https://geocode.arcgis.com/arcgis/rest/services/World/GeocodeServer/find: ERROR - HTTPSConnectionPool(host='geocode.arcgis.com', port=443): Read timed out. (read timeout=5.0)


done!


In [12]:
coordinates_df = pd.DataFrame(coordinates, columns = ['Latitude', 'Longitude'])
chicago_df['Latitude'] = coordinates_df['Latitude']
chicago_df['Longitude'] = coordinates_df['Longitude']

In [13]:
# making sure that the correct coordinates are being filled in
chicago_df[chicago_df.Neighborhood == 'Brighton Park']

State County     City   Neighborhood  Latitude  Longitude
0    IL   Cook  Chicago  Brighton Park  41.81861  -87.69948

In [14]:
# We can take a look at the dataframe and see that all neighborhoods now have their respective coordinates
chicago_df.head()

State County     City      Neighborhood  Latitude  Longitude
0    IL   Cook  Chicago     Brighton Park  41.81861  -87.69948
1    IL   Cook  Chicago  Stateway Gardens  41.82976  -87.62783
2    IL   Cook  Chicago        Ravenswood  41.96692  -87.66706
3    IL   Cook  Chicago   Parkway Gardens  41.77476  -87.61588
4    IL   Cook  Chicago       South Shore  41.76158  -87.57802

In [15]:
# create map of Chicago using latitude and longitude values
map_chicago = folium.Map(location=[latitude, longitude], zoom_start=11)

# add markers to map
for lat, lng, label in zip(chicago_df['Latitude'], chicago_df['Longitude'], chicago_df['Neighborhood']):
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_chicago)  
    
map_chicago

In [16]:
CLIENT_ID = 'JDF2X5TBDABYSNQYJ2R4ADGFSMIOZK3GJFK2UVKH1PC1QTVM' # your Foursquare ID
CLIENT_SECRET = 'NZAERTGGQUJ3YJW0FAJNQEZBC54E5FN35VV2F2PHS43GQFDV' # your Foursquare Secret
VERSION = '20180605' # Foursquare API version

print('Your credentails:')
print('CLIENT_ID: ' + CLIENT_ID)
print('CLIENT_SECRET:' + CLIENT_SECRET)

Your credentails:
CLIENT_ID: JDF2X5TBDABYSNQYJ2R4ADGFSMIOZK3GJFK2UVKH1PC1QTVM
CLIENT_SECRET:NZAERTGGQUJ3YJW0FAJNQEZBC54E5FN35VV2F2PHS43GQFDV


In [17]:
chicago_df.loc[0, 'Neighborhood']

'Brighton Park'

In [18]:
neighborhood_latitude = chicago_df.loc[0, 'Latitude'] # neighborhood latitude value
neighborhood_longitude = chicago_df.loc[0, 'Longitude'] # neighborhood longitude value

neighborhood_name = chicago_df.loc[0, 'Neighborhood'] # neighborhood name

print('Latitude and longitude values of {} are {}, {}.'.format(neighborhood_name, 
                                                               neighborhood_latitude, 
                                                               neighborhood_longitude))

Latitude and longitude values of Brighton Park are 41.818610000000035, -87.69947999999994.


In [19]:
# Get the top 100 venues within a 500 meter radius of Brighton Park
LIMIT = 100
radius = 500

url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
    CLIENT_ID, 
    CLIENT_SECRET, 
    VERSION, 
    neighborhood_latitude, 
    neighborhood_longitude, 
    radius, 
    LIMIT)

# This is what the entire GET request url will look like
url

'https://api.foursquare.com/v2/venues/explore?&client_id=JDF2X5TBDABYSNQYJ2R4ADGFSMIOZK3GJFK2UVKH1PC1QTVM&client_secret=NZAERTGGQUJ3YJW0FAJNQEZBC54E5FN35VV2F2PHS43GQFDV&v=20180605&ll=41.818610000000035,-87.69947999999994&radius=500&limit=100'

In [20]:
# send the GET request and examine the results
results = requests.get(url).json()

In [21]:
# function that extracts the category of the venue
def get_category_type(row):
    try:
        categories_list = row['categories']
    except:
        categories_list = row['venue.categories']
        
    if len(categories_list) == 0:
        return None
    else:
        return categories_list[0]['name']

In [22]:
# clean JSON and structure into a pandas dataframe
venues = results['response']['groups'][0]['items']
    
nearby_venues = json_normalize(venues) # flatten JSON

# filter columns
filtered_columns = ['venue.name', 'venue.categories', 'venue.location.lat', 'venue.location.lng']
nearby_venues =nearby_venues.loc[:, filtered_columns]

# filter the category for each row
nearby_venues['venue.categories'] = nearby_venues.apply(get_category_type, axis=1)

# clean columns
nearby_venues.columns = [col.split(".")[-1] for col in nearby_venues.columns]

nearby_venues.head()

name          categories        lat        lng
0                Paco's Tacos          Taco Place  41.815218 -87.702317
1                     Falco's         Pizza Place  41.820159 -87.694874
2  Tierra Caliente Restaurant  Mexican Restaurant  41.819614 -87.695495
3             La Fiesta Tacos          Taco Place  41.816260 -87.700876
4              Submarine Pier      Sandwich Place  41.820217 -87.694373

In [23]:
print('{} venues were returned by Foursquare.'.format(nearby_venues.shape[0]))

17 venues were returned by Foursquare.


In [24]:
# create a function to repeat the process for all neighborhoods in Chicago
def getNearbyVenues(names, latitudes, longitudes, radius=500):
    
    venues_list=[]
    for name, lat, lng in zip(names, latitudes, longitudes):
        print(name)
            
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            LIMIT)
            
        # make the GET request
        results = requests.get(url).json()["response"]['groups'][0]['items']
        
        # return only relevant information for each nearby venue
        venues_list.append([(
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Neighborhood', 
                  'Neighborhood Latitude', 
                  'Neighborhood Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    
    return(nearby_venues)

In [25]:
chicago_venues = getNearbyVenues(names=chicago_df['Neighborhood'],
                                   latitudes=chicago_df['Latitude'],
                                   longitudes=chicago_df['Longitude']
                                  )

Brighton Park
Stateway Gardens
Ravenswood
Parkway Gardens
South Shore
Washington Park
Hanson Park
Belmont Terrace
Heart of Italy
The Bush
Rogers Park
Clearing (E)
South Loop
Pulaski Park
Kilbourn Park
Gold Coast
Edgewater
Lake View East
Jefferson Park
Marquette Park
Grand Crossing
Andersonville
Noble Square
West Elsdon
Marynook
Pilsen
Oriole Park
Beverly Woods
Park West
Belmont Gardens
Magnolia Glen
Schorsch Village
Garfield Ridge
Palmer Square
Roscoe Village
River's Edge
South Austin
Hermosa
Near North
Dearborn Park
Rosemoor
Fulton River District
Goose Island
Little Calumet River
Ukrainian Village
West Garfield Park
Ashburn
Cottage Grove Heights
Chicago Midway Airport
Altgeld Gardens
Lincoln Square
Scottsdale
Trumbull Park
Heart of Chicago
West Rogers Park
Mount Greenwood Heights
North Kenwood
Arcadia Terrace
West Pullman
Wicker Park
Tri-Taylor
Sheffield Neighbors
Norwood Park East
Eden Green
Park Manor
Belmont Heights
South Deering
Stony Island Park
Canaryville
Burnside
Edison Park
L

In [26]:
print(chicago_venues.shape)
chicago_venues.head()

(6044, 7)


Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
0  Brighton Park               41.81861               -87.69948   
1  Brighton Park               41.81861               -87.69948   
2  Brighton Park               41.81861               -87.69948   
3  Brighton Park               41.81861               -87.69948   
4  Brighton Park               41.81861               -87.69948   

                        Venue  Venue Latitude  Venue Longitude  \
0                Paco's Tacos       41.815218       -87.702317   
1                     Falco's       41.820159       -87.694874   
2  Tierra Caliente Restaurant       41.819614       -87.695495   
3             La Fiesta Tacos       41.816260       -87.700876   
4              Submarine Pier       41.820217       -87.694373   

       Venue Category  
0          Taco Place  
1         Pizza Place  
2  Mexican Restaurant  
3          Taco Place  
4      Sandwich Place

In [27]:
# group to see how many venues were returned for each neighborhood
chicago_venues.groupby('Neighborhood').count()

Neighborhood Latitude  \
Neighborhood                                               
Albany Park                                           26   
Altgeld Gardens                                        2   
Andersonville                                         55   
Arcadia Terrace                                       10   
Archer Heights                                        22   
Ashburn                                                7   
Avalon Park                                           12   
Avondale                                              29   
Back of the Yards                                     17   
Belmont Central                                       17   
Belmont Gardens                                       32   
Belmont Heights                                       32   
Belmont Terrace                                       32   
Beverly                                                4   
Beverly View                                          12   
Beverly Woods                                          9   
Big Oaks                                             100   
Bowmanville                                           11   
Brainerd                                              10   
Bridgeport                                            40   
Brighton Park                                         17   
Bronzeville                                           10   
Brynford Park                                          4   
Bucktown                                              40   
Budlong Woods                                         95   
Buena Park                                            45   
Burnside                                               4   
Cabrini Green                                         44   
Calumet Heights                                        9   
Calumet River                                          2   
Canaryville                                           10   
Chatham                                                6   
Chicago Lawn                                          16   
Chicago Midway Airport                                42   
Chinatown                                             55   
Chrysler Village                                      15   
Clearing (E)                                          10   
Clearing (W)                                          10   
Cottage Grove Heights                                  4   
Cragin                                                11   
Dearborn Park                                         65   
Douglas Park                                           5   
Dunning                                                4   
East Beverly                                          12   
East Chatham                                           6   
East Garfield Park                                     9   
East Hyde Park                                        34   
East Pilsen                                           63   
East Side                                              4   
East Ukrainian Village                                61   
Eden Green                                            12   
Edgebrook                                             24   
Edgewater                                             40   
Edgewater Beach                                       49   
Edgewater Glen                                        43   
Edison Park                                            3   
Englewood                                             19   
Fernwood                                               3   
Fifth City                                             6   
Ford City                                             21   
Forest Glen                                           16   
Fuller Park                                           10   
Fulton River District                                 24   
Gage Park                                              9   
Galewood                                               8   
Garfield Ridge 

In [28]:
# get the number of unique categories that can be curated from all the returned venues
print('There are {} uniques categories.'.format(len(chicago_venues['Venue Category'].unique())))

There are 359 uniques categories.


In [29]:
# one hot encoding
chicago_onehot = pd.get_dummies(chicago_venues[['Venue Category']], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
chicago_onehot['Neighborhood'] = chicago_venues['Neighborhood'] 

# move neighborhood column to the first column
fixed_columns = [chicago_onehot.columns[-1]] + list(chicago_onehot.columns[:-1])
chicago_onehot = chicago_onehot[fixed_columns]

chicago_onehot.head()

Yoga Studio  ATM  Accessories Store  Adult Boutique  African Restaurant  \
0            0    0                  0               0                   0   
1            0    0                  0               0                   0   
2            0    0                  0               0                   0   
3            0    0                  0               0                   0   
4            0    0                  0               0                   0   

   Airport  Airport Food Court  Airport Lounge  Airport Service  \
0        0                   0               0                0   
1        0                   0               0                0   
2        0                   0               0                0   
3        0                   0               0                0   
4        0                   0               0                0   

   Airport Terminal  American Restaurant  Amphitheater  Animal Shelter  \
0                 0                    0             0               0   
1                 0                    0             0               0   
2                 0                    0             0               0   
3                 0                    0             0               0   
4                 0                    0             0               0   

   Antique Shop  Arcade  Arepa Restaurant  Argentinian Restaurant  \
0             0       0                 0                       0   
1             0       0                 0                       0   
2             0       0                 0                       0   
3             0       0                 0                       0   
4             0       0                 0                       0   

   Art Gallery  Art Museum  Arts & Crafts Store  Arts & Entertainment  \
0            0           0                    0                     0   
1            0           0                    0                     0   
2            0           0                    0                     0   
3            0           0                    0                     0   
4            0           0                    0                     0   

   Asian Restaurant  Athletics & Sports  Auto Dealership  Automotive Shop  \
0                 0                   0                0                0   
1                 0                   0                0                0   
2                 0                   0                0                0   
3                 0                   0                0                0   
4                 0                   0                0                0   

   BBQ Joint  Baby Store  Bagel Shop  Bakery  Bank  Bar  Baseball Field  \
0          0           0           0       0     0    0               0   
1          0           0           0       0     0    0               0   
2          0           0           0       0     0    0               0   
3          0           0           0       0     0    0               0   
4          0           0           0       0     0    0               0   

   Baseball Stadium  Basketball Court  Beach  Bed & Breakfast  Beer Bar  \
0                 0                 0      0                0         0   
1                 0                 0      0                0         0   
2                 0                 0      0                0         0   
3                 0                 0      0                0         0   
4                 0                 0      0                0         0   

   Beer Garden  Beer Store  Big Box Store  Bike Rental / Bike Share  \
0            0           0              0                         0   
1            0           0              0                         0   
2            0           0              0                         0   
3            0           0              0                         0   
4            0           0              0                         0   

   Bike Shop  Bike Trail  Bistro  Board 

In [30]:
# check the size of the dataframe
chicago_onehot.shape

(6044, 359)

In [31]:
# group rows by neighborhood and by taking the mean of the frequency of occurrence of each category
chicago_grouped = chicago_onehot.groupby('Neighborhood').mean().reset_index()
chicago_grouped

Neighborhood  Yoga Studio       ATM  \
0                          Albany Park     0.000000  0.000000   
1                      Altgeld Gardens     0.000000  0.000000   
2                        Andersonville     0.000000  0.000000   
3                      Arcadia Terrace     0.000000  0.000000   
4                       Archer Heights     0.000000  0.000000   
5                              Ashburn     0.000000  0.000000   
6                          Avalon Park     0.000000  0.083333   
7                             Avondale     0.000000  0.000000   
8                    Back of the Yards     0.000000  0.000000   
9                      Belmont Central     0.000000  0.000000   
10                     Belmont Gardens     0.000000  0.000000   
11                     Belmont Heights     0.000000  0.000000   
12                     Belmont Terrace     0.000000  0.000000   
13                             Beverly     0.000000  0.000000   
14                        Beverly View     0.000000  0.000000   
15                       Beverly Woods     0.000000  0.000000   
16                            Big Oaks     0.000000  0.000000   
17                         Bowmanville     0.000000  0.000000   
18                            Brainerd     0.000000  0.000000   
19                          Bridgeport     0.000000  0.000000   
20                       Brighton Park     0.000000  0.000000   
21                         Bronzeville     0.000000  0.000000   
22                       Brynford Park     0.000000  0.000000   
23                            Bucktown     0.025000  0.000000   
24                       Budlong Woods     0.021053  0.000000   
25                          Buena Park     0.000000  0.000000   
26                            Burnside     0.000000  0.000000   
27                       Cabrini Green     0.000000  0.000000   
28                     Calumet Heights     0.000000  0.000000   
29                       Calumet River     0.000000  0.000000   
30                         Canaryville     0.000000  0.000000   
31                             Chatham     0.000000  0.000000   
32                        Chicago Lawn     0.000000  0.000000   
33              Chicago Midway Airport     0.000000  0.000000   
34                           Chinatown     0.000000  0.000000   
35                    Chrysler Village     0.000000  0.000000   
36                        Clearing (E)     0.000000  0.000000   
37                        Clearing (W)     0.000000  0.000000   
38               Cottage Grove Heights     0.000000  0.000000   
39                              Cragin     0.000000  0.000000   
40                       Dearborn Park     0.015385  0.000000   
41                        Douglas Park     0.000000  0.000000   
42                             Dunning     0.000000  0.000000   
43                        East Beverly     0.000000  0.000000   
44                        East Chatham     0.000000  0.000000   
45                  East Garfield Park     0.000000  0.000000   
46                      East Hyde Park     0.000000  0.000000   
47                         East Pilsen     0.000000  0.000000   
48                           East Side     0.000000  0.000000   
49              East Ukrainian Village     0.000000  0.000000   
50                          Eden Green     0.000000  0.000000   
51                           Edgebrook     0.000000  0.000000   
52                           Edgewater     0.000000  0.000000   
53                     Edgewater Beach     0.000000  0.000000   
54                      Edgewater Glen     0.000000  0.000000   
55                         Edison Park     0.000000  0.000000   
56                           Englewood     0.000000  0.105263   
57                            Fernwood     0.000000  0.000000   
58                          Fifth City     0.000000  0.000000   
59                           Ford City     0.000000  0.000000   
60                         Forest Glen     0.000000  0.000000

In [32]:
chicago_grouped.shape

(227, 359)

In [33]:
num_top_venues = 5

for hood in chicago_grouped['Neighborhood']:
    print("----"+hood+"----")
    temp = chicago_grouped[chicago_grouped['Neighborhood'] == hood].T.reset_index()
    temp.columns = ['venue','freq']
    temp = temp.iloc[1:]
    temp['freq'] = temp['freq'].astype(float)
    temp = temp.round({'freq': 2})
    print(temp.sort_values('freq', ascending=False).reset_index(drop=True).head(num_top_venues))
    print('\n')

----Albany Park----
                venue  freq
0  Mexican Restaurant  0.12
1      Discount Store  0.08
2                Bank  0.08
3   Mobile Phone Shop  0.04
4          Hookah Bar  0.04


----Altgeld Gardens----
                  venue  freq
0                  Park   0.5
1  Fast Food Restaurant   0.5
2           Yoga Studio   0.0
3          Outlet Store   0.0
4  Outdoor Supply Store   0.0


----Andersonville----
                       venue  freq
0                Coffee Shop  0.07
1               Burger Joint  0.04
2  Middle Eastern Restaurant  0.04
3              Grocery Store  0.04
4                     Lounge  0.04


----Arcadia Terrace----
               venue  freq
0  Korean Restaurant   0.2
1               Park   0.1
2     Breakfast Spot   0.1
3           Pharmacy   0.1
4         Taco Place   0.1


----Archer Heights----
                  venue  freq
0    Mexican Restaurant  0.14
1     Mobile Phone Shop  0.14
2           Gas Station  0.09
3         Grocery Store  0.09
4  Gym / 

In [34]:
# write a function to sort the venues in descending order
def return_most_common_venues(row, num_top_venues):
    row_categories = row.iloc[1:]
    row_categories_sorted = row_categories.sort_values(ascending=False)
    
    return row_categories_sorted.index.values[0:num_top_venues]

In [35]:
# create a new dataframe and display the top 10 venues for each neighborhood
num_top_venues = 10

indicators = ['st', 'nd', 'rd']

# create columns according to number of top venues
columns = ['Neighborhood']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

# create a new dataframe
neighborhoods_venues_sorted = pd.DataFrame(columns=columns)
neighborhoods_venues_sorted['Neighborhood'] = chicago_grouped['Neighborhood']

for ind in np.arange(chicago_grouped.shape[0]):
    neighborhoods_venues_sorted.iloc[ind, 1:] = return_most_common_venues(chicago_grouped.iloc[ind, :], num_top_venues)

neighborhoods_venues_sorted.head()

Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
0      Albany Park    Mexican Restaurant                  Bank   
1  Altgeld Gardens  Fast Food Restaurant                  Park   
2    Andersonville           Coffee Shop                  Café   
3  Arcadia Terrace     Korean Restaurant     Convenience Store   
4   Archer Heights     Mobile Phone Shop    Mexican Restaurant   

   3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
0         Discount Store        Cosmetics Shop             Pet Store   
1  Entertainment Service         Event Service           Event Space   
2           Burger Joint    Italian Restaurant     Korean Restaurant   
3             Taco Place        Breakfast Spot                  Park   
4            Gas Station         Grocery Store         Hot Dog Joint   

       6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
0                Bus Station    Seafood Restaurant        Clothing Store   
1                    Exhibit            Eye Doctor               Factory   
2  Middle Eastern Restaurant        Sandwich Place         Grocery Store   
3        Japanese Restaurant              Pharmacy           Coffee Shop   
4                   Pharmacy        Sandwich Place                   Bar   

  9th Most Common Venue 10th Most Common Venue  
0           Coffee Shop             Playground  
1    Falafel Restaurant                   Farm  
2                Lounge             Comic Shop  
3              Tea Room          Event Service  
4  Gym / Fitness Center          Big Box Store

In [36]:
# set number of clusters
kclusters = 5

chicago_grouped_clustering = chicago_grouped.drop('Neighborhood', 1)

# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(chicago_grouped_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_[0:10] 

array([0, 4, 3, 3, 0, 3, 0, 3, 0, 0], dtype=int32)

In [37]:
# create a dataframe that includes the clster as well as the top 10 venues for each neighborhood

neighborhoods_venues_sorted.insert(0, 'Cluster Labels', kmeans.labels_)

chicago_merged = chicago_df

# merge toronto_grouped with toronto_data to add latitude/longitude for each neighborhood
chicago_merged = chicago_merged.join(neighborhoods_venues_sorted.set_index('Neighborhood'), on='Neighborhood')

chicago_merged.head() # check the last columns!

State County     City      Neighborhood  Latitude  Longitude  \
0    IL   Cook  Chicago     Brighton Park  41.81861  -87.69948   
1    IL   Cook  Chicago  Stateway Gardens  41.82976  -87.62783   
2    IL   Cook  Chicago        Ravenswood  41.96692  -87.66706   
3    IL   Cook  Chicago   Parkway Gardens  41.77476  -87.61588   
4    IL   Cook  Chicago       South Shore  41.76158  -87.57802   

   Cluster Labels 1st Most Common Venue 2nd Most Common Venue  \
0               0    Mexican Restaurant         Grocery Store   
1               3      Baseball Stadium            Sports Bar   
2               3            Taco Place           Bus Station   
3               3         Train Station             Locksmith   
4               3           Pizza Place            Playground   

  3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
0            Taco Place                  Park           Bus Station   
1        Shipping Store        Sandwich Place           Pizza Place   
2        Massage Studio                   Spa           Coffee Shop   
3                  Food           Music Venue           Bus Station   
4              Pharmacy        Baseball Field          Optical Shop   

  6th Most Common Venue 7th Most Common Venue  8th Most Common Venue  \
0          Burger Joint   American Restaurant  Check Cashing Service   
1        Clothing Store           Snack Place     Frozen Yogurt Shop   
2          Liquor Store               Theater             Board Shop   
3   American Restaurant  Fast Food Restaurant          Women's Store   
4         Grocery Store                  Park        Harbor / Marina   

  9th Most Common Venue 10th Most Common Venue  
0        Sandwich Place         Breakfast Spot  
1                   Bar                   Bank  
2           Gas Station       Sushi Restaurant  
3               Exhibit             Eye Doctor  
4                  Bank    American Restaurant

In [38]:
# create map
map_clusters = folium.Map(location=[latitude, longitude], zoom_start=11)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i + x + (i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(chicago_merged['Latitude'], chicago_merged['Longitude'], chicago_merged['Neighborhood'], chicago_merged['Cluster Labels']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[cluster-1],
        fill=True,
        fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(map_clusters)
       
map_clusters

In [39]:
chicago_merged.loc[chicago_merged['Cluster Labels'] == 0, chicago_merged.columns[[1] + list(range(5, chicago_merged.shape[1]))]]

County  Longitude  Cluster Labels 1st Most Common Venue  \
0     Cook -87.699480               0    Mexican Restaurant   
6     Cook -87.763390               0              Pharmacy   
23    Cook -87.723410               0    Mexican Restaurant   
25    Cook -87.657590               0    Mexican Restaurant   
27    Cook -87.680930               0                  Food   
31    Cook -87.791650               0     Polish Restaurant   
37    Cook -87.734240               0    Mexican Restaurant   
45    Cook -87.730740               0        Cosmetics Shop   
58    Cook -87.641890               0  Fast Food Restaurant   
64    Cook -87.618590               0  Fast Food Restaurant   
67    Cook -87.574490               0     Convenience Store   
76    Cook -87.673380               0                 Diner   
84    Cook -87.696340               0           Pizza Place   
87    Cook -87.723380               0    Mexican Restaurant   
89    Cook -87.695610               0     Convenience Store   
94    Cook -87.724450               0        Ice Cream Shop   
99    Cook -87.662730               0    Mexican Restaurant   
110   Cook -87.725560               0     Mobile Phone Shop   
116   Cook -87.710730               0            Eye Doctor   
119   Cook -87.683610               0                   Bar   
129   Cook -87.684550               0  Fast Food Restaurant   
150   Cook -87.657590               0    Mexican Restaurant   
156   Cook -87.711720               0    Mexican Restaurant   
158   Cook -87.775591               0    Mexican Restaurant   
161   Cook -87.667260               0  Fast Food Restaurant   
166   Cook -87.588160               0          Burger Joint   
170   Cook -87.791650               0     Polish Restaurant   
175   Cook -87.798470               0           Wings Joint   
176   Cook -87.756010               0    Mexican Restaurant   
181   Cook -87.659430               0           Coffee Shop   
193   Cook -87.737720               0  Fast Food Restaurant   
202   Cook -87.711720               0    Mexican Restaurant   
213   Cook -87.577420               0     Convenience Store   
221   Cook -87.777340               0    Mexican Restaurant   
223   Cook -87.536250               0    Seafood Restaurant   
227   Cook -87.789170               0   Sporting Goods Shop   

    2nd Most Common Venue       3rd Most Common Venue  \
0           Grocery Store                  Taco Place   
6        Cuban Restaurant                   Pet Store   
23         Ice Cream Shop                 Gas Station   
25                    Bar                      Bakery   
27             Playground              Breakfast Spot   
31       Czech Restaurant                 Gas Station   
37            Supermarket       Check Cashing Service   
45          Grocery Store              Discount Store   
58         Cosmetics Shop         American Restaurant   
64          Train Station              Farmers Market   
67     Mexican Restaurant  Construction & Landscaping   
76     Seafood Restaurant               Grocery Store   
84     Mexican Restaurant              Cosmetics Shop   
87                   Bank              Discount Store   
89     Mexican Restaurant            Asian Restaurant   
94          Bowling Alley        Fast Food Restaurant   
99          Grocery Store                        Bank   
110    Mexican Restaurant                 Gas Station   
116    Mexican Restaurant              Sandwich Place   
119        Cosmetics Shop                Skating Rink   
129          Intersection            Business Service   
150                   Bar                      Bakery   
156           Pizza Place                        Bank   
158     Convenience Store        Fast Food Restaurant   
161        Cosmetics Shop               Train Station   
166              Boutique        Fast Food Restaurant   
170      Czech Restaurant                 Gas Station   
175          Home Service  Financial or Legal Service   
176            Donu

In [40]:
chicago_merged.loc[chicago_merged['Cluster Labels'] == 1, chicago_merged.columns[[1] + list(range(5, chicago_merged.shape[1]))]]

County  Longitude  Cluster Labels 1st Most Common Venue  \
66    Cook -87.559510               1                   Bar   
90    Cook -90.064170               1                   Bar   
167   Cook -87.646201               1                  Food   
172   Cook -87.578940               1            Donut Shop   
189   Cook -87.646459               1                   Bar   

    2nd Most Common Venue 3rd Most Common Venue 4th Most Common Venue  \
66     Mexican Restaurant         Women's Store   Filipino Restaurant   
90          Women's Store  Ethiopian Restaurant           Event Space   
167                   Bar         Women's Store  Fast Food Restaurant   
172                   Bar         Women's Store  Fast Food Restaurant   
189        Cosmetics Shop         Bowling Alley   American Restaurant   

    5th Most Common Venue 6th Most Common Venue 7th Most Common Venue  \
66            Event Space               Exhibit            Eye Doctor   
90                Exhibit            Eye Doctor               Factory   
167           Event Space               Exhibit            Eye Doctor   
172           Event Space               Exhibit            Eye Doctor   
189      Basketball Court         Women's Store   Filipino Restaurant   

    8th Most Common Venue 9th Most Common Venue 10th Most Common Venue  
66                Factory    Falafel Restaurant                   Farm  
90     Falafel Restaurant                  Farm         Farmers Market  
167               Factory    Falafel Restaurant                   Farm  
172               Factory    Falafel Restaurant                   Farm  
189            Eye Doctor               Factory     Falafel Restaurant

In [41]:
chicago_merged.loc[chicago_merged['Cluster Labels'] == 2, chicago_merged.columns[[1] + list(range(5, chicago_merged.shape[1]))]]

County  Longitude  Cluster Labels 1st Most Common Venue  \
218   Cook  -87.62574               2          Intersection   

    2nd Most Common Venue 3rd Most Common Venue 4th Most Common Venue  \
218         Women's Store   Filipino Restaurant         Event Service   

    5th Most Common Venue 6th Most Common Venue 7th Most Common Venue  \
218           Event Space               Exhibit            Eye Doctor   

    8th Most Common Venue 9th Most Common Venue 10th Most Common Venue  
218               Factory    Falafel Restaurant                   Farm

In [42]:
chicago_merged.loc[chicago_merged['Cluster Labels'] == 3, chicago_merged.columns[[1] + list(range(5, chicago_merged.shape[1]))]]

County  Longitude  Cluster Labels      1st Most Common Venue  \
1       Cook -87.627830               3           Baseball Stadium   
2       Cook -87.667060               3                 Taco Place   
3       Cook -87.615880               3              Train Station   
4       Cook -87.578020               3                Pizza Place   
5       Cook -87.622390               3       Fast Food Restaurant   
7       Cook -87.831392               3         Salon / Barbershop   
8       Cook -87.632450               3             Sandwich Place   
9       Cook -87.632450               3             Sandwich Place   
10      Cook -87.666180               3                    Theater   
11      Cook -87.759780               3                 Sports Bar   
12      Cook -87.628840               3                Coffee Shop   
13      Cook -87.663920               3                Art Gallery   
14      Cook -87.739610               3            Thai Restaurant   
15      Cook -87.628860               3                       Café   
16      Cook -87.663460               3         Mexican Restaurant   
17      Cook -87.624328               3                      Hotel   
18      Cook -87.763460               3                    Theater   
20      Cook -87.599230               3                  BBQ Joint   
21      Cook -87.668340               3                Coffee Shop   
22      Cook -87.664650               3                        Bar   
24      Cook -87.653358               3             Clothing Store   
26      Cook -87.814430               3                        Gym   
29      Cook -87.831392               3         Salon / Barbershop   
30      Cook -87.661751               3                Coffee Shop   
32      Cook -87.770140               3                Wings Joint   
33      Cook -87.704780               3                   Dive Bar   
34      Cook -87.678490               3                Bus Station   
35      Cook -87.733236               3                Video Store   
36      Cook -87.771917               3                     Bakery   
38      Cook -87.635165               3                 Steakhouse   
39      Cook -87.628690               3                Pizza Place   
40      Cook -87.865416               3             Clothing Store   
41      Cook -87.686698               3        Rental Car Location   
42      Cook -87.652750               3                        Bar   
43      Cook -87.560880               3            Harbor / Marina   
44      Cook -87.682040               3                     Bakery   
46      Cook -87.709950               3             Cosmetics Shop   
47      Cook -87.608193               3              Historic Site   
48      Cook -87.742140               3                 Donut Shop   
50      Cook -87.689140               3                        Bar   
51      Cook -87.732240               3                     Bakery   
53      Cook -87.675381               3                    Brewery   
54      Cook -87.694140               3          Indian Restaurant   
55      Cook -87.708730               3                       Park   
56      Cook -87.593537               3                Bus Station   
57      Cook -87.709100               3          Korean Restaurant   
59      Cook -87.682960               3                Pizza Place   
60      Cook -87.686122               3         Italian Restaurant   
61      Cook -87.653488               3             Cosmetics Shop   
62      Cook -87.665260               3          Martial Arts Dojo   
63      Cook -87.699740               3          Convenience Store   
65      Cook -87.831392               3         Salon / Barbershop   
68      Cook -87.640870               3                Pizza Place   
71      Cook -87.761498               3                        Bar   
72      Cook -87.696890               3                 Restaurant   
73      Cook -87.596820               3                Bus Station   
74      Cook -87

In [43]:
chicago_merged.loc[chicago_merged['Cluster Labels'] == 4, chicago_merged.columns[[1] + list(range(5, chicago_merged.shape[1]))]]

County  Longitude  Cluster Labels 1st Most Common Venue  \
19    Cook -87.702990               4                  Park   
28    Cook -88.161040               4                  Park   
49    Cook -87.602250               4  Fast Food Restaurant   
52    Cook -87.565560               4                  Park   
69    Cook -87.597450               4                   Gym   
70    Cook -87.813990               4                  Park   
81    Cook -87.728670               4                  Park   
82    Cook -87.613030               4              Boutique   
83    Cook -88.161286               4                  Park   
88    Cook -87.806640               4                  Park   
95    Cook -87.672810               4         Souvenir Shop   
107   Cook -87.741334               4         Moving Target   
111   Cook -87.639040               4                  Park   
120   Cook -87.742270               4                  Park   
136   Cook -87.614167               4  Fast Food Restaurant   
149   Cook -88.314340               4                  Park   
153   Cook -87.796510               4      Indoor Play Area   
154   Cook -87.750390               4         Hot Dog Joint   
180   Cook -87.605650               4                  Park   
187   Cook -87.613030               4              Boutique   
200   Cook -87.610670               4                  Food   
204   Cook -87.613030               4              Boutique   
206   Cook -87.629660               4                  Pool   
209   Cook -87.605760               4                  Park   

       2nd Most Common Venue            3rd Most Common Venue  \
19      Fast Food Restaurant                      Gas Station   
28                 Mini Golf                   Breakfast Spot   
49                      Park            Entertainment Service   
52         Convenience Store                           Bakery   
69                      Park  Southern / Soul Food Restaurant   
70                   Theater                    Women's Store   
81            Gymnastics Gym                 Department Store   
82      Fast Food Restaurant                           Lounge   
83             Grocery Store                    Women's Store   
88             Women's Store            Entertainment Service   
95                  Platform                             Park   
107                     Park                            Trail   
111             Intersection                    Grocery Store   
120        Indian Restaurant                         Pharmacy   
136                Bookstore                             Park   
149                     Pool                            Trail   
153             Intersection                             Park   
154                     Park                          Parking   
180  Health & Beauty Service                         Boutique   
187     Fast Food Restaurant                           Lounge   
200                     Park                    Grocery Store   
204     Fast Food Restaurant                           Lounge   
206                     Park             Caribbean Restaurant   
209               Food Court                    National Park   

    4th Most Common Venue 5th Most Common Venue 6th Most Common Venue  \
19             Donut Shop           Event Space               Exhibit   
28          Women's Store  Fast Food Restaurant           Event Space   
49          Event Service           Event Space               Exhibit   
52         Farmers Market         Event Service           Event Space   
69                Dog Run        Farmers Market         Event Service   
70         Farmers Market  Ethiopian Restaurant         Event Service   
81   Kitchen Supply Store         Women's Store        Farmers Market   
82                   Park            Donut Shop         Women's Store   
83         Farmers Market  Ethiopian Restaurant         Event Service   
88          Event Service           Event Space               Exhibit   

In [44]:
#download the data from url
url = "https://en.wikipedia.org/wiki/List_of_postal_codes_of_Canada:_M"
res = requests.get(url).text
data = BeautifulSoup(res, 'lxml')
print('done!')

done!


In [45]:
#create dataframe
df_toronto = ['PostalCode','Borough','Neighborhood']
toronto = pd.DataFrame(columns = df_toronto)

#toronto.head()

table_data = data.find('div', class_ = 'mw-parser-output')
table = table_data.table.tbody

postcode = 0
borough = 0
neighborhood = 0

for tr in table.find_all('tr'):
    i = 0
    for td in tr.find_all('td'):
        if i == 0:
            postcode = td.text
            i = i+1
        elif i ==1:
            borough = td.text
            i = i+1
        elif i == 2:
            neighborhood = td.text.strip('\n').replace(']', '')
    toronto = toronto.append({'PostalCode': postcode, 'Borough' : borough, 'Neighborhood': neighborhood}, ignore_index = True)

print(toronto.shape)

(289, 3)


In [46]:
#Only process the cells that have an assigned borough - ignore cells with a borough that is Not assigned.
toronto = toronto[toronto.Borough!= 'Not assigned']
toronto = toronto[toronto.Borough!= 0]
toronto.reset_index(drop = True, inplace = True)

#If a cell has a borough but a "Not assigned" neighborhood, then the neighborhood will be the same as the borough.
i = 0
for i in range(0,toronto.shape[0]):
    if toronto.iloc[i][2] == 'Not assigned':
        toronto.iloc[i][2] = toronto.iloc[i][1]
        i = i+1

#Group postalcodes that have multiple neighborhoods and display neighborhoods with a comma seperation
df = toronto.groupby(['PostalCode', 'Borough'])['Neighborhood'].apply(', '.join).reset_index()
df.head()
#print(df.shape)

PostalCode      Borough                            Neighborhood
0        M1B  Scarborough                          Rouge, Malvern
1        M1C  Scarborough  Highland Creek, Rouge Hill, Port Union
2        M1E  Scarborough       Guildwood, Morningside, West Hill
3        M1G  Scarborough                                  Woburn
4        M1H  Scarborough                               Cedarbrae

In [47]:
#Drop any "none" or "not assigned" values
df = df.dropna()
blank = 'Not assigned'
df = df[(df.PostalCode != blank) & (df.Borough != blank) & (df.Neighborhood != blank)]
df.head(10)

PostalCode      Borough                                     Neighborhood
0        M1B  Scarborough                                   Rouge, Malvern
1        M1C  Scarborough           Highland Creek, Rouge Hill, Port Union
2        M1E  Scarborough                Guildwood, Morningside, West Hill
3        M1G  Scarborough                                           Woburn
4        M1H  Scarborough                                        Cedarbrae
5        M1J  Scarborough                              Scarborough Village
6        M1K  Scarborough      East Birchmount Park, Ionview, Kennedy Park
7        M1L  Scarborough                  Clairlea, Golden Mile, Oakridge
8        M1M  Scarborough  Cliffcrest, Cliffside, Scarborough Village West
9        M1N  Scarborough                      Birch Cliff, Cliffside West

In [48]:
print(df.shape)

(103, 3)


In [49]:
#Read in the Geospatial_Coordinates.csv file
import pandas
geospatial_df = pd.read_csv("Geospatial_Coordinates.csv")
geospatial_df.set_index(['Postal Code', 'Latitude', 'Longitude'])

#renaming the columns to do an inner join on the next step
geospatial_df.columns = ['PostalCode', 'Latitude', 'Longitude']
geospatial_df.head(10)

PostalCode   Latitude  Longitude
0        M1B  43.806686 -79.194353
1        M1C  43.784535 -79.160497
2        M1E  43.763573 -79.188711
3        M1G  43.770992 -79.216917
4        M1H  43.773136 -79.239476
5        M1J  43.744734 -79.239476
6        M1K  43.727929 -79.262029
7        M1L  43.711112 -79.284577
8        M1M  43.716316 -79.239476
9        M1N  43.692657 -79.264848

In [50]:
#inner join on postalcodes to get the latitude and longitude in the same dataframe
df_geo = pd.merge(df,geospatial_df, on='PostalCode', how='inner')
df_geo.head()

PostalCode      Borough                            Neighborhood   Latitude  \
0        M1B  Scarborough                          Rouge, Malvern  43.806686   
1        M1C  Scarborough  Highland Creek, Rouge Hill, Port Union  43.784535   
2        M1E  Scarborough       Guildwood, Morningside, West Hill  43.763573   
3        M1G  Scarborough                                  Woburn  43.770992   
4        M1H  Scarborough                               Cedarbrae  43.773136   

   Longitude  
0 -79.194353  
1 -79.160497  
2 -79.188711  
3 -79.216917  
4 -79.239476

In [51]:
#Searching for boroughs that contain the word Toronto
df_toronto = df_geo[df_geo['Borough'].str.contains('Toronto')]
df_toronto = df_toronto.reset_index(drop=True)
df_toronto.head()

PostalCode          Borough                    Neighborhood   Latitude  \
0        M4E     East Toronto                     The Beaches  43.676357   
1        M4K     East Toronto    The Danforth West, Riverdale  43.679557   
2        M4L     East Toronto  The Beaches West, India Bazaar  43.668999   
3        M4M     East Toronto                 Studio District  43.659526   
4        M4N  Central Toronto                   Lawrence Park  43.728020   

   Longitude  
0 -79.293031  
1 -79.352188  
2 -79.315572  
3 -79.340923  
4 -79.388790

In [52]:
address = 'Toronto'

geolocator = Nominatim()
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinates of Toronto are {}, {}.'.format(latitude, longitude))

/home/jupyterlab/conda/envs/python/lib/python3.6/site-packages/ipykernel_launcher.py:3: DeprecationWarning: Using Nominatim with the default "geopy/1.20.0" `user_agent` is strongly discouraged, as it violates Nominatim's ToS https://operations.osmfoundation.org/policies/nominatim/ and may possibly cause 403 and 429 HTTP errors. Please specify a custom `user_agent` with `Nominatim(user_agent="my-application")` or by overriding the default `user_agent`: `geopy.geocoders.options.default_user_agent = "my-application"`. In geopy 2.0 this will become an exception.
  This is separate from the ipykernel package so we can avoid doing imports until


The geograpical coordinates of Toronto are 43.653963, -79.387207.


In [53]:
# create map of Toronto using latitude and longitude values
map_toronto = folium.Map(location=[latitude, longitude], zoom_start=11)

# add markers to map
for lat, lng, label in zip(df_toronto['Latitude'], df_toronto['Longitude'], df_toronto['Neighborhood']):
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='green',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_toronto)  
    
map_toronto

In [54]:
df_toronto.loc[0, 'Neighborhood']

'The Beaches'

In [55]:
neighborhood_latitude = df_toronto.loc[0, 'Latitude'] # neighborhood latitude value
neighborhood_longitude = df_toronto.loc[0, 'Longitude'] # neighborhood longitude value

neighborhood_name = df_toronto.loc[0, 'Neighborhood'] # neighborhood name

print('Latitude and longitude values of {} are {}, {}.'.format(neighborhood_name, 
                                                               neighborhood_latitude, 
                                                               neighborhood_longitude))

Latitude and longitude values of The Beaches are 43.67635739999999, -79.2930312.


In [56]:
#Top 100 venues that are in 'The Beaches' around 500 meters 
LIMIT = 100
radius = 500

url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
    CLIENT_ID, 
    CLIENT_SECRET, 
    VERSION, 
    neighborhood_latitude, 
    neighborhood_longitude, 
    radius, 
    LIMIT)

url

'https://api.foursquare.com/v2/venues/explore?&client_id=JDF2X5TBDABYSNQYJ2R4ADGFSMIOZK3GJFK2UVKH1PC1QTVM&client_secret=NZAERTGGQUJ3YJW0FAJNQEZBC54E5FN35VV2F2PHS43GQFDV&v=20180605&ll=43.67635739999999,-79.2930312&radius=500&limit=100'

In [57]:
results = requests.get(url).json()
results

{'meta': {'code': 200, 'requestId': '5d9e2a7b475abd002ce4dfa9'},
 'response': {'headerLocation': 'The Beaches',
  'headerFullLocation': 'The Beaches, Toronto',
  'headerLocationGranularity': 'neighborhood',
  'totalResults': 4,
  'suggestedBounds': {'ne': {'lat': 43.680857404499996,
    'lng': -79.28682091449052},
   'sw': {'lat': 43.67185739549999, 'lng': -79.29924148550948}},
  'groups': [{'type': 'Recommended Places',
    'name': 'recommended',
    'items': [{'reasons': {'count': 0,
       'items': [{'summary': 'This spot is popular',
         'type': 'general',
         'reasonName': 'globalInteractionReason'}]},
      'venue': {'id': '4bd461bc77b29c74a07d9282',
       'name': 'Glen Manor Ravine',
       'location': {'address': 'Glen Manor',
        'crossStreet': 'Queen St.',
        'lat': 43.67682094413784,
        'lng': -79.29394208780985,
        'labeledLatLngs': [{'label': 'display',
          'lat': 43.67682094413784,
          'lng': -79.29394208780985}],
        'distanc

In [58]:
# function that extracts the category of the venue
def get_category_type(row):
    try:
        categories_list = row['categories']
    except:
        categories_list = row['venue.categories']
        
    if len(categories_list) == 0:
        return None
    else:
        return categories_list[0]['name']

In [59]:
#structure the data into a pandas dataframe
venues = results['response']['groups'][0]['items']
    
nearby_venues = json_normalize(venues) # flatten JSON

# filter columns
filtered_columns = ['venue.name', 'venue.categories', 'venue.location.lat', 'venue.location.lng']
nearby_venues =nearby_venues.loc[:, filtered_columns]

# filter the category for each row
nearby_venues['venue.categories'] = nearby_venues.apply(get_category_type, axis=1)

# clean columns
nearby_venues.columns = [col.split(".")[-1] for col in nearby_venues.columns]

nearby_venues.head(10)
#print('{} venues were returned by Foursquare.'.format(nearby_venues.shape[0]))

name         categories        lat        lng
0                   Glen Manor Ravine              Trail  43.676821 -79.293942
1  The Big Carrot Natural Food Market  Health Food Store  43.678879 -79.297734
2                 Grover Pub and Grub                Pub  43.679181 -79.297215
3                       Upper Beaches       Neighborhood  43.680563 -79.292869

In [60]:
def getNearbyVenues(names, latitudes, longitudes, radius=500):
    
    venues_list=[]
    for name, lat, lng in zip(names, latitudes, longitudes):
        print(name)
            
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            LIMIT)
            
        # make the GET request
        results = requests.get(url).json()["response"]['groups'][0]['items']
        
        # return only relevant information for each nearby venue
        venues_list.append([(
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Neighborhood', 
                  'Neighborhood Latitude', 
                  'Neighborhood Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    
    return(nearby_venues)

In [61]:
toronto_venues = getNearbyVenues(names=df_toronto['Neighborhood'],
                                   latitudes=df_toronto['Latitude'],
                                   longitudes=df_toronto['Longitude']
                                  )

The Beaches
The Danforth West, Riverdale
The Beaches West, India Bazaar
Studio District
Lawrence Park
Davisville North
North Toronto West
Davisville
Moore Park, Summerhill East
Deer Park, Forest Hill SE, Rathnelly, South Hill, Summerhill West
Rosedale
Cabbagetown, St. James Town
Church and Wellesley
Harbourfront, Regent Park
Ryerson, Garden District
St. James Town
Berczy Park
Central Bay Street
Adelaide, King, Richmond
Harbourfront East, Toronto Islands, Union Station
Design Exchange, Toronto Dominion Centre
Commerce Court, Victoria Hotel
Roselawn
Forest Hill North, Forest Hill West
The Annex, North Midtown, Yorkville
Harbord, University of Toronto
Chinatown, Grange Park, Kensington Market
CN Tower, Bathurst Quay, Island airport, Harbourfront West, King and Spadina, Railway Lands, South Niagara
Stn A PO Boxes 25 The Esplanade
First Canadian Place, Underground city
Christie
Dovercourt Village, Dufferin
Little Portugal, Trinity
Brockton, Exhibition Place, Parkdale Village
High Park, The 

In [62]:
#check the size of the datadframe and print out the first 20 rows
print(toronto_venues.shape)
toronto_venues.head(20)

(1711, 7)


Neighborhood  Neighborhood Latitude  \
0                    The Beaches              43.676357   
1                    The Beaches              43.676357   
2                    The Beaches              43.676357   
3                    The Beaches              43.676357   
4   The Danforth West, Riverdale              43.679557   
5   The Danforth West, Riverdale              43.679557   
6   The Danforth West, Riverdale              43.679557   
7   The Danforth West, Riverdale              43.679557   
8   The Danforth West, Riverdale              43.679557   
9   The Danforth West, Riverdale              43.679557   
10  The Danforth West, Riverdale              43.679557   
11  The Danforth West, Riverdale              43.679557   
12  The Danforth West, Riverdale              43.679557   
13  The Danforth West, Riverdale              43.679557   
14  The Danforth West, Riverdale              43.679557   
15  The Danforth West, Riverdale              43.679557   
16  The Danforth West, Riverdale              43.679557   
17  The Danforth West, Riverdale              43.679557   
18  The Danforth West, Riverdale              43.679557   
19  The Danforth West, Riverdale              43.679557   

    Neighborhood Longitude                               Venue  \
0               -79.293031                   Glen Manor Ravine   
1               -79.293031  The Big Carrot Natural Food Market   
2               -79.293031                 Grover Pub and Grub   
3               -79.293031                       Upper Beaches   
4               -79.352188                            Pantheon   
5               -79.352188                       MenEssentials   
6               -79.352188                        Dolce Gelato   
7               -79.352188                     Cafe Fiorentina   
8               -79.352188                          La Diperie   
9               -79.352188              Louis Cifer Brew Works   
10              -79.352188                               Mezes   
11              -79.352188             Messini Authentic Gyros   
12              -79.352188                   The Auld Spot Pub   
13              -79.352188                Moksha Yoga Danforth   
14              -79.352188    The Big Carrot Organic Juice Bar   
15              -79.352188                 Valley Farm Produce   
16              -79.352188                          Alexandros   
17              -79.352188                   Pizzeria Libretto   
18              -79.352188                       Caffé Demetre   
19              -79.352188                           7 Numbers   

    Venue Latitude  Venue Longitude           Venue Category  
0        43.676821       -79.293942                    Trail  
1        43.678879       -79.297734        Health Food Store  
2        43.679181       -79.297215                      Pub  
3        43.680563       -79.292869             Neighborhood  
4        43.677621       -79.351434         Greek Restaurant  
5        43.677820       -79.351265           Cosmetics Shop  
6        43.677773       -79.351187           Ice Cream Shop  
7        43.677743       -79.350115       Italian Restaurant  
8        43.677530       -79.352295           Ice Cream Shop  
9        43.677663       -79.351313                  Brewery  
10       43.677962       -79.350196         Greek Restaurant  
11       43.677827       -79.350569         Greek Restaurant  
12       43.677335       -79.353130                      Pub  
13       43.677622       -79.352116              Yoga Studio  
14       43.677438       -79.352683                Juice Bar  
15       43.677999       -79.349969  Fruit & Vegetable Store  
16       43.678304       -79.349486         Greek Restaurant  
17       43.678489       -79.347576              Pizza Place  
18       43.677683       -79.351608             Dessert Shop  
19       43.677062       -79.353934       Italian Restaurant

In [63]:
toronto_venues.groupby('Neighborhood').count()

Neighborhood Latitude  \
Neighborhood                                                                
Adelaide, King, Richmond                                              100   
Berczy Park                                                            57   
Brockton, Exhibition Place, Parkdale Village                           22   
Business Reply Mail Processing Centre 969 Eastern                      20   
CN Tower, Bathurst Quay, Island airport, Harbou...                     15   
Cabbagetown, St. James Town                                            45   
Central Bay Street                                                     84   
Chinatown, Grange Park, Kensington Market                             100   
Christie                                                               16   
Church and Wellesley                                                   87   
Commerce Court, Victoria Hotel                                        100   
Davisville                                                             32   
Davisville North                                                        7   
Deer Park, Forest Hill SE, Rathnelly, South Hil...                     16   
Design Exchange, Toronto Dominion Centre                              100   
Dovercourt Village, Dufferin                                           15   
First Canadian Place, Underground city                                100   
Forest Hill North, Forest Hill West                                     4   
Harbord, University of Toronto                                         36   
Harbourfront East, Toronto Islands, Union Station                     100   
Harbourfront, Regent Park                                              50   
High Park, The Junction South                                          23   
Lawrence Park                                                           3   
Little Portugal, Trinity                                               68   
Moore Park, Summerhill East                                             3   
North Toronto West                                                     20   
Parkdale, Roncesvalles                                                 15   
Rosedale                                                                5   
Roselawn                                                                2   
Runnymede, Swansea                                                     35   
Ryerson, Garden District                                              100   
St. James Town                                                        100   
Stn A PO Boxes 25 The Esplanade                                       100   
Studio District                                                        40   
The Annex, North Midtown, Yorkville                                    24   
The Beaches                                                             4   
The Beaches West, India Bazaar                                         21   
The Danforth West, Riverdale                                           42   

                                                    Neighborhood Longitude  \
Neighborhood                                                                 
Adelaide, King, Richmond                                               100   
Berczy Park                                                             57   
Brockton, Exhibition Place, Parkdale Village                            22   
Business Reply Mail Processing Centre 969 Eastern                       20   
CN Tower, Bathurst Quay, Island airport, Harbou...                      15   
Cabbagetown, St. James Town                                             45   
Central Bay Street                                                      84   
Chinatown, Grange Park, Kensington Market                              100   
Christie                                                                16   
Church and Wellesley                                                    87   
Commerce Court, Victoria Hotel     

In [64]:
#see how many unique categories can be curated from the returned values
print('There are {} uniques categories.'.format(len(toronto_venues['Venue Category'].unique())))

There are 237 uniques categories.


In [65]:
# one hot encoding
toronto_onehot = pd.get_dummies(toronto_venues[['Venue Category']], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
toronto_onehot['Neighborhood'] = toronto_venues['Neighborhood'] 

# move neighborhood column to the first column
fixed_columns = [toronto_onehot.columns[-1]] + list(toronto_onehot.columns[:-1])
toronto_onehot = toronto_onehot[fixed_columns]

toronto_onehot.head()

Yoga Studio  Afghan Restaurant  Airport  Airport Food Court  Airport Gate  \
0            0                  0        0                   0             0   
1            0                  0        0                   0             0   
2            0                  0        0                   0             0   
3            0                  0        0                   0             0   
4            0                  0        0                   0             0   

   Airport Lounge  Airport Service  Airport Terminal  American Restaurant  \
0               0                0                 0                    0   
1               0                0                 0                    0   
2               0                0                 0                    0   
3               0                0                 0                    0   
4               0                0                 0                    0   

   Antique Shop  Aquarium  Art Gallery  Art Museum  Arts & Crafts Store  \
0             0         0            0           0                    0   
1             0         0            0           0                    0   
2             0         0            0           0                    0   
3             0         0            0           0                    0   
4             0         0            0           0                    0   

   Asian Restaurant  Athletics & Sports  Auto Workshop  BBQ Joint  Baby Store  \
0                 0                   0              0          0           0   
1                 0                   0              0          0           0   
2                 0                   0              0          0           0   
3                 0                   0              0          0           0   
4                 0                   0              0          0           0   

   Bagel Shop  Bakery  Bank  Bar  Baseball Stadium  Basketball Stadium  Beach  \
0           0       0     0    0                 0                   0      0   
1           0       0     0    0                 0                   0      0   
2           0       0     0    0                 0                   0      0   
3           0       0     0    0                 0                   0      0   
4           0       0     0    0                 0                   0      0   

   Bed & Breakfast  Beer Bar  Beer Store  Belgian Restaurant  Bistro  \
0                0         0           0                   0       0   
1                0         0           0                   0       0   
2                0         0           0                   0       0   
3                0         0           0                   0       0   
4                0         0           0                   0       0   

   Board Shop  Boat or Ferry  Bookstore  Boutique  Brazilian Restaurant  \
0           0              0          0         0                     0   
1           0              0          0         0                     0   
2           0              0          0         0                     0   
3           0              0          0         0                     0   
4           0              0          0         0                     0   

   Breakfast Spot  Brewery  Bubble Tea Shop  Building  Burger Joint  \
0               0        0                0         0             0   
1               0        0                0         0             0   
2               0        0                0         0             0   
3               0        0                0         0             0   
4               0        0                0         0             0   

   Burrito Place  Bus Line  Butcher  Café  Cajun / Creole Restaurant  \
0              0         0        0     0                          0   
1              0         0        0     0                          0   
2              0         0        0     0                          0   
3              0         0        0

In [66]:
#view the size of this onehot dataframe
toronto_onehot.shape

(1711, 237)

In [67]:
toronto_grouped = toronto_onehot.groupby('Neighborhood').mean().reset_index()
toronto_grouped

Neighborhood  Yoga Studio  \
0                            Adelaide, King, Richmond     0.000000   
1                                         Berczy Park     0.000000   
2        Brockton, Exhibition Place, Parkdale Village     0.000000   
3   Business Reply Mail Processing Centre 969 Eastern     0.050000   
4   CN Tower, Bathurst Quay, Island airport, Harbo...     0.000000   
5                         Cabbagetown, St. James Town     0.000000   
6                                  Central Bay Street     0.011905   
7           Chinatown, Grange Park, Kensington Market     0.000000   
8                                            Christie     0.000000   
9                                Church and Wellesley     0.011494   
10                     Commerce Court, Victoria Hotel     0.000000   
11                                         Davisville     0.000000   
12                                   Davisville North     0.000000   
13  Deer Park, Forest Hill SE, Rathnelly, South Hi...     0.000000   
14           Design Exchange, Toronto Dominion Centre     0.000000   
15                       Dovercourt Village, Dufferin     0.000000   
16             First Canadian Place, Underground city     0.000000   
17                Forest Hill North, Forest Hill West     0.000000   
18                     Harbord, University of Toronto     0.027778   
19  Harbourfront East, Toronto Islands, Union Station     0.000000   
20                          Harbourfront, Regent Park     0.020000   
21                      High Park, The Junction South     0.000000   
22                                      Lawrence Park     0.000000   
23                           Little Portugal, Trinity     0.014706   
24                        Moore Park, Summerhill East     0.000000   
25                                 North Toronto West     0.050000   
26                             Parkdale, Roncesvalles     0.000000   
27                                           Rosedale     0.000000   
28                                           Roselawn     0.000000   
29                                 Runnymede, Swansea     0.000000   
30                           Ryerson, Garden District     0.000000   
31                                     St. James Town     0.000000   
32                    Stn A PO Boxes 25 The Esplanade     0.000000   
33                                    Studio District     0.025000   
34                The Annex, North Midtown, Yorkville     0.000000   
35                                        The Beaches     0.000000   
36                     The Beaches West, India Bazaar     0.000000   
37                       The Danforth West, Riverdale     0.023810   

    Afghan Restaurant   Airport  Airport Food Court  Airport Gate  \
0            0.000000  0.000000            0.000000      0.000000   
1            0.000000  0.000000            0.000000      0.000000   
2            0.000000  0.000000            0.000000      0.000000   
3            0.000000  0.000000            0.000000      0.000000   
4            0.000000  0.066667            0.066667      0.066667   
5            0.000000  0.000000            0.000000      0.000000   
6            0.000000  0.000000            0.000000      0.000000   
7            0.000000  0.000000            0.000000      0.000000   
8            0.000000  0.000000            0.000000      0.000000   
9            0.011494  0.000000            0.000000      0.000000   
10           0.000000  0.000000            0.000000      0.000000   
11           0.000000  0.000000            0.000000      0.000000   
12           0.000000  0.000000            0.000000      0.000000   
13           0.000000  0.000000            0.000000      0.000000   
14           0.000000  0.000000            0.000000      0.000000   
15           0.000000  0.000000            0.000000      0.000000   
16           0.000000  0.000000            0.000000      0.000000   
17           0.000000  0.000000            0.000000      0.000000   

In [68]:
#confirm the new size of the dataframe
toronto_grouped.shape

(38, 237)

In [69]:
num_top_venues = 5

for hood in toronto_grouped['Neighborhood']:
    print("----"+hood+"----")
    temp = toronto_grouped[toronto_grouped['Neighborhood'] == hood].T.reset_index()
    temp.columns = ['venue','freq']
    temp = temp.iloc[1:]
    temp['freq'] = temp['freq'].astype(float)
    temp = temp.round({'freq': 2})
    print(temp.sort_values('freq', ascending=False).reset_index(drop=True).head(num_top_venues))
    print('\n')

----Adelaide, King, Richmond----
                 venue  freq
0          Coffee Shop  0.08
1                 Café  0.05
2                  Bar  0.04
3  American Restaurant  0.04
4      Thai Restaurant  0.04


----Berczy Park----
            venue  freq
0     Coffee Shop  0.07
1    Cocktail Bar  0.05
2      Steakhouse  0.04
3            Café  0.04
4  Farmers Market  0.04


----Brockton, Exhibition Place, Parkdale Village----
            venue  freq
0  Breakfast Spot  0.09
1     Coffee Shop  0.09
2            Café  0.09
3      Restaurant  0.05
4   Grocery Store  0.05


----Business Reply Mail Processing Centre 969 Eastern----
                venue  freq
0  Light Rail Station  0.10
1         Yoga Studio  0.05
2         Pizza Place  0.05
3          Skate Park  0.05
4             Brewery  0.05


----CN Tower, Bathurst Quay, Island airport, Harbourfront West, King and Spadina, Railway Lands, South Niagara----
              venue  freq
0    Airport Lounge  0.13
1   Airport Service  0.13
2    

In [70]:
def return_most_common_venues(row, num_top_venues):
    row_categories = row.iloc[1:]
    row_categories_sorted = row_categories.sort_values(ascending=False)
    
    return row_categories_sorted.index.values[0:num_top_venues]

In [78]:
num_top_venues = 10

indicators = ['st', 'nd', 'rd']

# create columns according to number of top venues
columns = ['Neighborhood']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

# create a new dataframe
neighborhoods_venues_sorted = pd.DataFrame(columns=columns)
neighborhoods_venues_sorted['Neighborhood'] = toronto_grouped['Neighborhood']

for ind in np.arange(toronto_grouped.shape[0]):
    neighborhoods_venues_sorted.iloc[ind, 1:] = return_most_common_venues(toronto_grouped.iloc[ind, :], num_top_venues)

neighborhoods_venues_sorted.head()

Neighborhood 1st Most Common Venue  \
0                           Adelaide, King, Richmond           Coffee Shop   
1                                        Berczy Park           Coffee Shop   
2       Brockton, Exhibition Place, Parkdale Village        Breakfast Spot   
3  Business Reply Mail Processing Centre 969 Eastern    Light Rail Station   
4  CN Tower, Bathurst Quay, Island airport, Harbo...        Airport Lounge   

  2nd Most Common Venue 3rd Most Common Venue 4th Most Common Venue  \
0                  Café                   Bar       Thai Restaurant   
1          Cocktail Bar                  Café           Cheese Shop   
2                  Café           Coffee Shop             Pet Store   
3           Yoga Studio      Recording Studio               Butcher   
4       Airport Service         Boat or Ferry       Harbor / Marina   

  5th Most Common Venue 6th Most Common Venue 7th Most Common Venue  \
0   American Restaurant            Steakhouse                 Hotel   
1            Steakhouse    Seafood Restaurant        Farmers Market   
2  Caribbean Restaurant               Stadium        Sandwich Place   
3            Restaurant         Auto Workshop                   Spa   
4              Boutique                   Bar           Coffee Shop   

  8th Most Common Venue 9th Most Common Venue 10th Most Common Venue  
0      Asian Restaurant            Restaurant           Burger Joint  
1              Beer Bar                Bakery      Indian Restaurant  
2         Burrito Place            Restaurant           Climbing Gym  
3  Fast Food Restaurant        Farmers Market             Smoke Shop  
4                 Plane      Sculpture Garden                Airport

In [79]:
# set number of clusters
kclusters = 5

toronto_grouped_clustering = toronto_grouped.drop('Neighborhood', 1)

# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(toronto_grouped_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_[0:10] 

array([0, 0, 0, 0, 0, 0, 0, 0, 0, 0], dtype=int32)

In [80]:
# add clustering labels
neighborhoods_venues_sorted.insert(0, 'Cluster Labels', kmeans.labels_)

toronto_merged = df_toronto

# merge toronto_grouped with toronto_data to add latitude/longitude for each neighborhood
toronto_merged = toronto_merged.join(neighborhoods_venues_sorted.set_index('Neighborhood'), on='Neighborhood')

toronto_merged.head() # check the last columns!

PostalCode          Borough                    Neighborhood   Latitude  \
0        M4E     East Toronto                     The Beaches  43.676357   
1        M4K     East Toronto    The Danforth West, Riverdale  43.679557   
2        M4L     East Toronto  The Beaches West, India Bazaar  43.668999   
3        M4M     East Toronto                 Studio District  43.659526   
4        M4N  Central Toronto                   Lawrence Park  43.728020   

   Longitude  Cluster Labels 1st Most Common Venue 2nd Most Common Venue  \
0 -79.293031               0     Health Food Store                 Trail   
1 -79.352188               0      Greek Restaurant           Coffee Shop   
2 -79.315572               0        Sandwich Place           Pizza Place   
3 -79.340923               0                  Café           Coffee Shop   
4 -79.388790               3              Bus Line                  Park   

  3rd Most Common Venue 4th Most Common Venue   5th Most Common Venue  \
0                   Pub           Wings Joint              Donut Shop   
1        Ice Cream Shop    Italian Restaurant  Furniture / Home Store   
2        Ice Cream Shop          Liquor Store                 Brewery   
3                Bakery    Italian Restaurant     American Restaurant   
4           Swim School           Wings Joint      Falafel Restaurant   

  6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
0                 Diner        Discount Store               Dog Run   
1                Bakery     Indian Restaurant            Sports Bar   
2            Board Shop          Burger Joint  Fast Food Restaurant   
3           Cheese Shop                  Bank                   Bar   
4           Event Space  Ethiopian Restaurant     Electronics Store   

         9th Most Common Venue       10th Most Common Venue  
0             Doner Restaurant  Eastern European Restaurant  
1                          Spa                    Juice Bar  
2                Burrito Place            Fish & Chips Shop  
3    Middle Eastern Restaurant                        Diner  
4  Eastern European Restaurant          Dumpling Restaurant

In [81]:
# create map
map_clusters = folium.Map(location=[latitude, longitude], zoom_start=11)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i + x + (i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(toronto_merged['Latitude'], toronto_merged['Longitude'], toronto_merged['Neighborhood'], toronto_merged['Cluster Labels']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[cluster-1],
        fill=True,
        fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(map_clusters)
       
map_clusters

In [82]:
toronto_merged.loc[toronto_merged['Cluster Labels'] == 0, toronto_merged.columns[[1] + list(range(5, toronto_merged.shape[1]))]]

Borough  Cluster Labels 1st Most Common Venue  \
0       East Toronto               0     Health Food Store   
1       East Toronto               0      Greek Restaurant   
2       East Toronto               0        Sandwich Place   
3       East Toronto               0                  Café   
5    Central Toronto               0                   Gym   
6    Central Toronto               0   Sporting Goods Shop   
7    Central Toronto               0          Dessert Shop   
9    Central Toronto               0           Coffee Shop   
11  Downtown Toronto               0           Coffee Shop   
12  Downtown Toronto               0           Coffee Shop   
13  Downtown Toronto               0           Coffee Shop   
14  Downtown Toronto               0           Coffee Shop   
15  Downtown Toronto               0                  Café   
16  Downtown Toronto               0           Coffee Shop   
17  Downtown Toronto               0           Coffee Shop   
18  Downtown Toronto               0           Coffee Shop   
19  Downtown Toronto               0           Coffee Shop   
20  Downtown Toronto               0           Coffee Shop   
21  Downtown Toronto               0           Coffee Shop   
23   Central Toronto               0                 Trail   
24   Central Toronto               0        Sandwich Place   
25  Downtown Toronto               0                  Café   
26  Downtown Toronto               0                  Café   
27  Downtown Toronto               0        Airport Lounge   
28  Downtown Toronto               0           Coffee Shop   
29  Downtown Toronto               0           Coffee Shop   
30  Downtown Toronto               0         Grocery Store   
31      West Toronto               0              Pharmacy   
32      West Toronto               0                   Bar   
33      West Toronto               0        Breakfast Spot   
34      West Toronto               0                  Café   
35      West Toronto               0        Breakfast Spot   
36      West Toronto               0           Coffee Shop   
37      East Toronto               0    Light Rail Station   

            2nd Most Common Venue    3rd Most Common Venue  \
0                           Trail                      Pub   
1                     Coffee Shop           Ice Cream Shop   
2                     Pizza Place           Ice Cream Shop   
3                     Coffee Shop                   Bakery   
5               Food & Drink Shop                     Park   
6                  Clothing Store              Coffee Shop   
7                  Sandwich Place         Sushi Restaurant   
9                             Pub  Health & Beauty Service   
11                      Pet Store               Restaurant   
12               Sushi Restaurant      Japanese Restaurant   
13                           Park                     Café   
14                 Clothing Store           Cosmetics Shop   
15                    Coffee Shop               Restaurant   
16                   Cocktail Bar                     Café   
17                           Café       Italian Restaurant   
18                           Café                      Bar   
19                          Hotel                 Aquarium   
20                           Café                    Hotel   
21                          Hotel                     Café   
23             Mexican Restaurant            Jewelry Store   
24                           Café              Pizza Place   
25                            Bar           Sandwich Place   
26  Vegetarian / Vegan Restaurant       Chinese Restaurant   
27                Airport Service            Boat or Ferry   
28                           Café               Restaurant   
29                           Café                    Hotel   
30                           Café                     Park   
31                    Supermarket                   Bakery   
32                    Men's Store           

In [83]:
toronto_merged.loc[toronto_merged['Cluster Labels'] == 1, toronto_merged.columns[[1] + list(range(5, toronto_merged.shape[1]))]]

Borough  Cluster Labels 1st Most Common Venue  \
8  Central Toronto               1                   Gym   

  2nd Most Common Venue 3rd Most Common Venue 4th Most Common Venue  \
8            Playground                 Trail           Wings Joint   

  5th Most Common Venue 6th Most Common Venue 7th Most Common Venue  \
8   Dumpling Restaurant                 Diner        Discount Store   

  8th Most Common Venue 9th Most Common Venue 10th Most Common Venue  
8               Dog Run      Doner Restaurant             Donut Shop

In [84]:
toronto_merged.loc[toronto_merged['Cluster Labels'] == 2, toronto_merged.columns[[1] + list(range(5, toronto_merged.shape[1]))]]

Borough  Cluster Labels 1st Most Common Venue  \
22  Central Toronto               2                  Pool   

   2nd Most Common Venue 3rd Most Common Venue 4th Most Common Venue  \
22                Garden           Wings Joint          Dessert Shop   

   5th Most Common Venue 6th Most Common Venue 7th Most Common Venue  \
22    Falafel Restaurant           Event Space  Ethiopian Restaurant   

   8th Most Common Venue        9th Most Common Venue 10th Most Common Venue  
22     Electronics Store  Eastern European Restaurant    Dumpling Restaurant

In [85]:
toronto_merged.loc[toronto_merged['Cluster Labels'] == 3, toronto_merged.columns[[1] + list(range(5, toronto_merged.shape[1]))]]

Borough  Cluster Labels 1st Most Common Venue  \
4  Central Toronto               3              Bus Line   

  2nd Most Common Venue 3rd Most Common Venue 4th Most Common Venue  \
4                  Park           Swim School           Wings Joint   

  5th Most Common Venue 6th Most Common Venue 7th Most Common Venue  \
4    Falafel Restaurant           Event Space  Ethiopian Restaurant   

  8th Most Common Venue        9th Most Common Venue 10th Most Common Venue  
4     Electronics Store  Eastern European Restaurant    Dumpling Restaurant

In [86]:
toronto_merged.loc[toronto_merged['Cluster Labels'] == 4, toronto_merged.columns[[1] + list(range(5, toronto_merged.shape[1]))]]

Borough  Cluster Labels 1st Most Common Venue  \
10  Downtown Toronto               4                  Park   

   2nd Most Common Venue 3rd Most Common Venue 4th Most Common Venue  \
10            Playground                 Trail              Building   

   5th Most Common Venue 6th Most Common Venue 7th Most Common Venue  \
10           Wings Joint            Donut Shop                 Diner   

   8th Most Common Venue 9th Most Common Venue 10th Most Common Venue  
10        Discount Store               Dog Run       Doner Restaurant